### Load a TCX file, display and analyze

In [1]:
import pandas as pd

# maps
import folium

from utility import load_df_from_tcx, compute_total_distance

In [2]:
POWER = False
CADENCE = False

In [3]:
F_NAME = "luigi_activity_12744958370.tcx"

df = load_df_from_tcx(F_NAME, cadence=False, power=False, debug=False)

df['timestamp'] = pd.to_datetime(df['timestamp'])

In [4]:
df.head(10)

id                 timestamp        position_lat       position_long  \
0   1 2023-11-15 17:13:51+00:00   41.93637407384813   12.46370242908597   
1   2 2023-11-15 17:13:52+00:00  41.936393436044455  12.463683234527707   
2   3 2023-11-15 17:13:53+00:00  41.936409026384354  12.463661944493651   
3   4 2023-11-15 17:13:54+00:00  41.936426209285855    12.4636404030025   
4   5 2023-11-15 17:13:55+00:00   41.93644054234028  12.463616011664271   
5   6 2023-11-15 17:13:56+00:00   41.93645428866148  12.463592123240232   
6   7 2023-11-15 17:13:57+00:00   41.93646837025881  12.463574856519699   
7   8 2023-11-15 17:13:58+00:00  41.936485301703215    12.4635627027601   
8   9 2023-11-15 17:13:59+00:00   41.93650055676699  12.463545938953757   
9  10 2023-11-15 17:14:00+00:00   41.93651287816465  12.463527247309685   

   altitude  distance  speed  heart_rate  
0    -500.0      0.00   0.00        94.0  
1    -500.0      2.72   2.85        94.0  
2    -500.0      5.21   8.67        94.0  
3    -500.0      7.66   8.83        94.0  
4    -500.0     10.54   8.90        95.0  
5    -500.0     12.90   8.83        96.0  
6    -500.0     15.17   8.13        97.0  
7    -500.0     17.24   7.86        98.0  
8    -500.0     19.57   7.86        99.0  
9    -500.0     21.60   8.77       100.0

#### Compute Statistics

In [5]:
all_cols = df.columns
exc_cols = ['id','timestamp','position_lat','position_long']
allow_cols = list(set(all_cols) - set(exc_cols))

# ignored first row, with counts
pd.set_option('display.precision', 1)

df[allow_cols].describe()[1:]

heart_rate  altitude  distance  speed
mean       140.2    -402.8    4796.3    8.7
std         16.5     983.4    2644.8    5.7
min         94.0    -500.0       0.0    0.0
25%        130.0    -500.0    2576.6    3.3
50%        144.0    -500.0    4695.6    9.1
75%        152.0    -500.0    7134.7   14.8
max        172.0   11000.0    9499.5   19.2

In [6]:
# remove when lat, long are nan
df = df.dropna(ignore_index=True)

# time elapsed
time_diff = df['timestamp'].iloc[-1] - df['timestamp'].iloc[0]

print(f"Elapsed time: {time_diff}")

# tot km
tot_km = round(compute_total_distance(df)/1000., 2)

print(f"Tot km. travelled: {tot_km}")

# va aggiunto il metabolismo basale (sono solo le calorie portate ai pedali)
# enhanced using eff factor (default = 0.25)
# we're assuming time between points is 1 sec.
if POWER:
    print(f"Tot active cal. consumed: {compute_energy_consumed(df, 'power'):.0f} kcal.")

Elapsed time: 0 days 01:11:32
Tot km. travelled: 9.5


In [7]:
# remove eventually rows where lat, lon are nan
df = df.dropna(ignore_index=True)

m = folium.Map(location=[df['position_lat'][1], df['position_long'][1]], zoom_start=15)

# to create the popup
cols_list = ['position_lat', 'position_long', 'altitude', 'speed', 'heart_rate']
if POWER:
    cols_list.append('power')
if CADENCE:
    cols_list.append('cadence')
    
for i, row in df[cols_list].iterrows():
    f_str = f"<b>Altitude: {row['altitude']:.1f} m.</b><br><b>Speed: {row['speed']:.1f} kmh</b><br><b>HR: {row['heart_rate']:.0f}</b>"

    if POWER:
        f_str += f"<br><b>Power: {row['power']} w."
    if CADENCE:
        f_str += f"<br><b>Cadence: {row['cadence']}"
        
    popup_html = folium.Popup(f_str, max_width=200)
    
    folium.CircleMarker(location=[row['position_lat'], row['position_long']],
                        popup=popup_html,
                        radius=3).add_to(m)

n_rows = i

# add start (green) end (red)
folium.CircleMarker(
    location=[df['position_lat'][0], df['position_long'][0]],  # Latitude and Longitude
    radius=5,  # Size of the circle
    color='green',  # Border color of the circle
    fill=True,
    fill_color='green'  # Fill color of the circle
).add_to(m)
folium.CircleMarker(
    location=[df['position_lat'][n_rows], df['position_long'][n_rows]],  # Latitude and Longitude
    radius=5,  # Size of the circle
    color='red',  # Border color of the circle
    fill=True,
    fill_color='red'  # Fill color of the circle
).add_to(m)

# display the map
m